In [2]:
from app.services.audio.audio import AudioSlicer
import pandas as pd
import json

In [3]:
import redis

redis_client = redis.Redis(host='localhost', port=6399, db=0,decode_responses=True)

from pathlib import  Path
import io
from faster_whisper import WhisperModel
import pandas as pd

Path.ls = lambda self:[item for item in self.iterdir()]

In [4]:
model_size = "large"
model = WhisperModel(model_size, device="cuda", compute_type="float16")

In [5]:
audio_path = Path('/home/andrew/volumes/audio')
#audio_path = Path('/home/dima/ssd/0/audio')
audio_path.exists()

True

In [7]:
redis_client.delete('diarizer')
redis_client.delete('transcriber')

0

In [8]:
from pathlib import Path
from typing import List

def list_files(directory: str, sort_by_time_desc: bool = True) -> List[Path]:
    files = [f for f in Path(directory).glob('*') if f.is_file()]
    return sorted(files, key=lambda x: x.stat().st_mtime, reverse=sort_by_time_desc) if sort_by_time_desc else files


In [9]:
import random

In [10]:
audio_file_path = Path('/home/andrew/volumes/audio/dd421e44-b243-4665-88c5-2c156687ddc8.webm')

In [11]:
#audio_file_path = random.choice(list_files(audio_path));audio_file_path

In [12]:
audio = await AudioSlicer.from_ffmpeg_slice(audio_file_path, 0, 300)
audio.audio

In [13]:
redis_client.set('path',str(audio_file_path))

True

In [14]:
import numpy as np

In [15]:
async def trnscribe(path,start,duration,last=''):
    audio_slicer = await AudioSlicer.from_ffmpeg_slice(path, start, duration)
    audio_data = await audio_slicer.export_data()
    segments, _ = model.transcribe(io.BytesIO(audio_data), beam_size=5, vad_filter=True, word_timestamps=True,initial_prompt=last)#,language='en'
    return [s for s in list(segments)],audio_slicer

In [16]:
# start_timestamp = pd.Timestamp.utcnow()
# redis_client.set('start_timestamp',start_timestamp.isoformat())
seek_timestamp =  pd.Timestamp(redis_client.get('start_timestamp'))

In [17]:
seek = 0
chunk_len = 20
step = 20

In [18]:
for _ in range(20):
    seek_timestamp = (seek_timestamp+pd.Timedelta(seconds=(step)))
    
    segments,audio_slicer = await trnscribe(audio_file_path, seek, chunk_len)
    result = list(segments)

    
    redis_client.lpush('transcriber',json.dumps((result,seek_timestamp.isoformat())))

    seek+=step